In [1]:
import pandas as pd
import numpy as np 
import os 
from time import time
import random 
random.seed(0)
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from nltk.stem.snowball import SnowballStemmer
from sklearn.metrics import accuracy_score
import nltk
from tqdm import tqdm
from pprint import pprint
from multiprocessing import Pool
from nltk.tokenize import TreebankWordTokenizer
from multiprocessing import Pool
from pandarallel import pandarallel
pandarallel.initialize(progress_bar=True)
print("Loaded all models")

INFO: Pandarallel will run on 4 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.
Loaded all models


In [2]:
def tok(txt):
    txt=txt.lower()
    return tokenizer.tokenize(txt)

In [3]:
def question_count(x):
    features={}
    q1=x['q1']
    q2=x['q2']
    q1_count=q1.count('?')
    q2_count=q2.count('?')
    question_count=q2_count-q1_count
    
    q1_intersection=[1 if x in q2 else 0 for x in q1]
    q1_intersection=sum(q1_intersection)/len(q1)
    
    q2_intersection=[1 if x in q1 else 0 for x in q2]
    q2_intersection=sum(q2_intersection)/len(q2)
    
    x['q1_ques_count']=q1_count
    x['q2_ques_count']=q2_count
    x['questions_count_diff']=question_count
    x['q1_norm_intersection']=q1_intersection
    x['q2_norm_intersection']=q2_intersection
    x['q1len']=len(q1)
    x['q2len']=len(q2)
    x['length_diff']=len(q2)-len(q1)
    x['q1_norm_len']=len(q1)/len(q2)
    x['q2_norm_len']=len(q2)/len(q1)
    return x

In [4]:
def checkNumbers(x):
    q1_num=[]
    q2_num=[]
    q1=eval(x.q1)
    for i in q1:
        if re.match("\d+",i):
            cleaned_string=re.sub("[^A-Za-z0-9]+","",i)
            number=re.findall("\d+",cleaned_string)
            q1_num.extend(number)
    q2=eval(x.q2)
    for i in q2:
        if re.match("\d+",i):
            cleaned_string=re.sub("[^A-Za-z0-9]+","",i)
            number=re.findall("\d+",cleaned_string)
            q2_num.extend(number)
    x={}

    x['q1_num_count']=len(q1_num)
    x['q2_num_count']=len(q2_num)
    
    q1_intersection=[x for x in q1_num if x in q2_num]
    q2_intersection=[x for x in q2_num if x in q1_num]
    
    x['q1_common_numbers']=len(q1_intersection)
    x['q2_common_numbers']=len(q2_intersection)
    
    if len(q1_num)==0 or len(q1_intersection)==0:
        x['q1_common_numbers_norm']=float(0)
    else:
        x['q1_common_numbers_norm']=len(q1_intersection)/len(q1_num)
        
    if len(q2_num)==0 or len(q2_intersection)==0:
        x['q2_common_numbers_norm']=float(0)
    else:
        x['q2_common_numbers_norm']=len(q2_intersection)/len(q2_num)
    return x

In [5]:
df=pd.read_csv("train.csv")
df.drop(['id','qid1','qid2'],inplace=True,axis=1)
df.dropna(inplace=True)
print(type(df))
df.head(5)

<class 'pandas.core.frame.DataFrame'>


question1  \
0  What is the step by step guide to invest in sh...   
1  What is the story of Kohinoor (Koh-i-Noor) Dia...   
2  How can I increase the speed of my internet co...   
3  Why am I mentally very lonely? How can I solve...   
4  Which one dissolve in water quikly sugar, salt...   

                                           question2  is_duplicate  
0  What is the step by step guide to invest in sh...             0  
1  What would happen if the Indian government sto...             0  
2  How can Internet speed be increased by hacking...             0  
3  Find the remainder when [math]23^{24}[/math] i...             0  
4            Which fish would survive in salt water?             0

In [ ]:
tokenizer=TreebankWordTokenizer()

p=Pool(4)
start=time()
df['q1']=p.map(tok,df.question1)
print(f"Time taken:{time()-start}")
p.close()
p.join()

In [ ]:
p=Pool(4)
start=time()
df['q2']=p.map(tok,df.question2)
print(f"Time taken:{time()-start}")
p.close()
p.join()

In [ ]:
df=df.parallel_apply(question_count,axis=1)

In [ ]:
features=df.parallel_apply(checkNumbers,axis=1)
features_df=pd.DataFrame(list(features))
df=pd.concat([df,features_df],axis=1)

In [5]:
def getPosTags(x):
    global counter
    print(counter)
    counter+=1
    x=eval(x)
    tags=nltk.pos_tag(x,tagset="universal")
    ref=pd.DataFrame(tags,columns=['token','tag'])
    ref['count']=1
    ref=ref.groupby(['tag'])['count'].sum().reset_index()
    ref.set_index('tag',inplace=True)
    out=ref.to_dict()['count']
    return out


In [ ]:
counter=0
output1=df.q1.apply(getPosTags)

In [ ]:
output1=list(output1)
df1=pd.DataFrame(output1)
df1.head()

In [ ]:
df1.fillna(0,inplace=True)
df1.to_csv("pos1.csv",index=None)
df1.head()

In [ ]:
counter=0
output2=df.q2.apply(getPosTags)

In [ ]:
output2=list(output2)
df2=pd.DataFrame(output2)
df2.head()

In [ ]:
df2.fillna(0,inplace=True)
df2.to_csv("pos2.csv",index=None)
df2.head()

In [ ]:
pos1=pd.read_csv("pos1.csv")
columns=["q1"+x for x in pos1.columns]
pos1.columns=columns

In [ ]:
pos2=pd.read_csv("pos2.csv")
columns=["q2"+x for x in pos2.columns]
pos2.columns=columns
pos2.columns

In [ ]:
print(df.shape)
df=pd.concat([df,pos1,pos2],axis=1)
print(ref.shape)
print(df.columns)

In [7]:
posiou=pd.read_csv("posiou.csv")
df=pd.concat([df,posiou],axis=1)

In [8]:
diff_columns=['.', 'ADP', 'ADV', 'DET', 'NOUN', 'PRON', 'PRT', 'VERB', 'ADJ', 'NUM',
       'CONJ', 'X']

In [9]:
for i in diff_columns:
    df["diff"+i]=df["q2"+i]-df["q1"+i]

In [10]:
ner_df=pd.read_csv("NER.csv")
ner_df.shape

(404287, 54)

In [11]:
print(df.shape)
df=pd.concat([df,ner_df],axis=1)
print(df.shape)
print(df.columns)

(404287, 63)
(404287, 117)
Index(['question1', 'question2', 'is_duplicate', 'q1', 'q2', 'q1_ques_count',
       'q2_ques_count', 'questions_count_diff', 'q1_norm_intersection',
       'q2_norm_intersection',
       ...
       'iouLANGUAGE', 'iouMONEY', 'iouLOC', 'iouWORK_OF_ART', 'iouQUANTITY',
       'iouEVENT', 'iouPERCENT', 'iouLAW', 'iouPRODUCT', 'iouFAC'],
      dtype='object', length=117)


In [12]:
Y=df['is_duplicate']
df.drop(['is_duplicate'],axis=1,inplace=True)
X=df.copy()

In [13]:
train, test, ytrain, ytest = train_test_split(X,Y,random_state=0,shuffle=True,test_size=0.1)

In [14]:
print(df.columns)
unwanted_cols=['question1','question2','q1','q2']
print(train[[x for x in train.columns if x not in unwanted_cols]].columns)

Index(['question1', 'question2', 'q1', 'q2', 'q1_ques_count', 'q2_ques_count',
       'questions_count_diff', 'q1_norm_intersection', 'q2_norm_intersection',
       'q1len',
       ...
       'iouLANGUAGE', 'iouMONEY', 'iouLOC', 'iouWORK_OF_ART', 'iouQUANTITY',
       'iouEVENT', 'iouPERCENT', 'iouLAW', 'iouPRODUCT', 'iouFAC'],
      dtype='object', length=116)
Index(['q1_ques_count', 'q2_ques_count', 'questions_count_diff',
       'q1_norm_intersection', 'q2_norm_intersection', 'q1len', 'q2len',
       'length_diff', 'q1_norm_len', 'q2_norm_len',
       ...
       'iouLANGUAGE', 'iouMONEY', 'iouLOC', 'iouWORK_OF_ART', 'iouQUANTITY',
       'iouEVENT', 'iouPERCENT', 'iouLAW', 'iouPRODUCT', 'iouFAC'],
      dtype='object', length=112)


In [15]:
clf=RandomForestClassifier(n_estimators=100,criterion="entropy",min_samples_split=10,oob_score=True,
                          n_jobs=4,random_state=0,verbose=1,class_weight="balanced")
clf.fit(train[[x for x in train.columns if x not in unwanted_cols]],ytrain)

[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   29.5s
[Parallel(n_jobs=4)]: Done 100 out of 100 | elapsed:  1.1min finished


RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight='balanced',
                       criterion='entropy', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=10,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=4,
                       oob_score=True, random_state=0, verbose=1,
                       warm_start=False)

In [16]:
pred=clf.predict(test[[x for x in train.columns if x not in unwanted_cols]])
# pred[pred>=0.5]=1

[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 100 out of 100 | elapsed:    1.0s finished


In [ ]:
output_df=test[['question1','question2']]
output_df['is_duplicate']=ytest
output_df['pred']=pred
output_df.to_csv("text_predictions.csv",index=None)

In [18]:
pred[pred>=0.5]=1

In [19]:
acc=accuracy_score(pred,ytest)
print(f"Accuracy of the model is {acc}")

Accuracy of the model is 0.7737762497217344


In [20]:
test['pred']=pred
test['orig']=ytest

diff=test[test['pred']==test['orig']]
for i in diff.itertuples():
    print("="*25)
    print(i.question1)
    print(i.question2)
    print(f"Original:{i.orig}")
    print(f"Predicted:{i.pred}")

/home/ravi/.local/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/ravi/.local/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


What are the best Doctor Doom stories?
What are the best comics featuring Doctor Doom?
Original:1
Predicted:1
What are the best books to prepare for SSB?
What are the best books to prepare for the IIT JAM physics exam?
Original:0
Predicted:0
Is an MS in VLSI from Portland State University good? I have heard Intel has a research center on its campus, is that true?
Which universities should I apply for an MS in VLSI?
Original:0
Predicted:0
Height: How would a 14 year old increase his height?
How should I increase my height?
Original:1
Predicted:1
What happened if we use diesel in petrol engine?
Which is worse for the engine, putting diesel in a "petrol car" or petrol in a "diesel car"?
Original:0
Predicted:0
Which is the best Harry Potter film and why?
Which is your favourite Harry Potter movie and why?
Original:1
Predicted:1
Despite Billion people, Why India is so bad at Olympics? Why does India lack talent?
Why India is so bad at Olympics? Is it because India is poor?
Original:1
Predic

What is the first brand of soupless instant noodles?
How is seeding of a hurricane done?
Original:0
Predicted:0
Why is it about anchovies that make them so expensive?
What makes a Daybed comforter set so expensive?
Original:0
Predicted:0
Which animal is considered to be the most curious in nature and why?
What are some animals that are considered dangerous but are actually timid and/or curious?
Original:0
Predicted:0
Why doesn't Pakistan arrest Hafiz Saeed?
Why is Pakistan did not arrest Hafiz Saeed, who is the mastermind behind 2008 Mumbai Terror Attacks?
Original:1
Predicted:1
Can an IPS (SP,SSP) give orders to an IAS (ADM, DM,DC) or its only vice versa?
Who are the best IAS/IPS officers India has seen?
Original:0
Predicted:0
Is mobbing at the workplace common in Germany, Austria and Switzerland? Since all have a welfare system, do companies have rules to prevent it?
If you were married, planning to have two children and are a single income household working in south Germany, would y

What is a charity?
What is charity?
Original:1
Predicted:1
Why is it seen as OK or understandable to be racist against white people?
Why is it OK for Quora users to call me racist for no reason, but not OK for me to say it's possible to be racist against white people?
Original:1
Predicted:1
How can I break wrong habits?
What are the best ways to break habits?
Original:1
Predicted:1
If we heat water, among hydrogen and oxygen which one is going to evaporated?
What would happen if we threw a bottle of water onto the moon?
Original:0
Predicted:0
How do I gain access to a private Instagram account?
How do I view someone's private Instagram pictures?
Original:1
Predicted:1
Which episode of Games of Thrones did not have sex scenes?
I heard that the CGI dragon scenes in Game of Thrones cost anywhere from $1,000,000 to $2,000,000 per episode. Is that accurate?
Original:0
Predicted:0
Is it okay to use your phone in a sauna?
Is it okay to wear my glasses when I'm using my phone?
Original:0
Predi

Predicted:0
Why do bad things seem to happen to good people?
Why does good things happen to bad people and why bad things happen to good people?
Original:1
Predicted:1
Does cough syrup contains sugar?
Why is alcohol used in cough syrups?
Original:0
Predicted:0
Is CBSE sports certificate is valid for sports quota jobs?
Is pro wrestling fake?
Original:0
Predicted:0
Where can I read One Piece Manga online?
I have been watching one piece for about 9 years. If I wanted to start reading the Manga should I start at the beginning?
Original:0
Predicted:0
How many GPS and/or heart rate enabled watches are being sold each year around the world?
How many watch branches are there in the world?
Original:0
Predicted:0
Can users follow my secondary blogs? Where can I view my followers?
Which are the best Indian Snapchat users to follow?
Original:0
Predicted:0
How do you get the molecular geometry of SCN?
What is the molecular geometry shape of the BF4- ion?
Original:0
Predicted:0
How do you rank the s

...

How can I become more patient?
How can anyone become patient?
Original:1
Predicted:1
How would the situation affect technology allows the nation's production possibilities curve more efficiently convert solar energy to electricity?
As a teacher (Or a student) has anyone fooled you/outsmarted you as a teacher?
Original:0
Predicted:0
How do you cook sausage links in a microwave?
What is the best way to cook Bratwurst sausages in a stove?
Original:0
Predicted:0
How can I convert JSON format string into a real object in JS?
What do I need and how to convert Java objects in JSON in Java?
Original:0
Predicted:0
Are there any treatments for lung cancer using nebulizers and breathing in medicines or healthy substances?
Which is the best website to start freelancing in node.js?
Original:0
Predicted:0
How does Apple Pay work?
How does Apple Pay integrate with Uber?
Original:0
Predicted:0
Can I produce electricity and sell it to the government?
If I produce electricity will government will buy it

How will Trump’s presidency affect international students in the US?
Original:0
Predicted:0
Which is best laptop to buy under 30k?
Which will be the best budget laptop under 30k?
Original:1
Predicted:1
How do I improve the habit of waking up early in the morning?
How can I make waking up earlier a habit?
Original:1
Predicted:1
Why did Trump Help Hillary win the election?
What are the chances that Trump is throwing the race so Hillary wins the election?
Original:1
Predicted:1
How do I get more Facebook page like?
How do I get enough likes on my Facebook page?
Original:1
Predicted:1
Who would win in a fight between Superman Prime and Galactus? Why?
You have a list of superheroes to choose from - one will protect you while the others try to kill you. Whom would you choose?
Original:0
Predicted:0
What are some of the best 7th grade science fair projects you've seen?
What are some examples of 7th grade science fair projects?
Original:1
Predicted:1
Are there more lesbians than gay men?
What 

Predicted:1
What is the meaning of I 7?
What does 3.7 x 4.1 mean?
Original:0
Predicted:0
What are some colors that go with aqua?
What colors go well with a pewter couch?
Original:0
Predicted:0
What is the future of the Go programming language?
Go (programming language): Why should the Linux kernel be rewritten in Go?
Original:0
Predicted:0
What is rollback attack?
Can panic attacks cause heart attacks?
Original:0
Predicted:0
Can I do intermittent fasting?
How do I intermittent fast? 
Original:0
Predicted:0
Ow many molecules are in 5 moles of h2o?
How many molecules are in 5 moles of h2o?
Original:1
Predicted:1
What are the benefits to ending a URL with the slash character.
Who was Ben hur?
Original:0
Predicted:0
I've been eating about 500 calories a day for years but don't get hungry. How can I make myself get hungrier/make eating easier?
Why does eating plain salad make me hungrier?
Original:0
Predicted:0
Where can I find cheap hotels in Las Vegas?
Where can I book cheap hotel rooms o

What is difference between an iPod and an iPad?
What is the difference between an iPhone, iPad, and iPod?
Original:0
Predicted:0
What is the best way to win a women's heart?
How do I win a girl's heart?
Original:1
Predicted:1
Is it possible make time machine?
Is it possible that one day a time machine would be created?
Original:1
Predicted:1
Why do dogs pee on vehicle tyres?
Why do dogs urinate on tree or vehicle tyres?
Original:1
Predicted:1
What is the full form of CISF to BSF in the Indian Army?
Is chinese army better than indian army?
Original:0
Predicted:0
What are the best smartphones under 15K in 2016?
Which is best smartphone to buy under Rs 15000?
Original:1
Predicted:1
What is NAFTA and what was it designed to accomplish?
What is NAFTA and why was it created?
Original:1
Predicted:1
Why don't Pakistan arrest Syed Mohammed Yusuf Shah (aka Syed Salahudeen),the head of the Hizb-ul-Mujahideen, when whole world knows he's a terrorist?
Why was this tweet from the fake profile of Pak

Original:0
Predicted:0
Which is the best institute for CAT in chandigarh?
Which is the best coaching institute for CAT in chandigarh?
Original:1
Predicted:1
What is Hajmola, really?
How bad can excessive Hajmola consumption be?
Original:0
Predicted:0
What can I do if I hate my life?
What should I do if I hate my life?
Original:1
Predicted:1
What do Chinese people want for China?
What do Chinese people want?
Original:0
Predicted:0
Why do we idolize Thomas Edison, when Nikola Tesla's alternate current is the most commonly used current?
How much truth is there in the Thomas Edison versus Nikola Tesla debate?
Original:0
Predicted:0
Which is a suitable inpatient drug and alcohol rehab center in Tift County GA?
Which is a suitable inpatient drug and alcohol rehab center in Bartow County GA?
Original:0
Predicted:0
Which company has compass logo?
What are the little known things about some famous logos?
Original:0
Predicted:0
What are the best plans for a healthy young person to choose from on

In [21]:
diff=test[test['pred']!=test['orig']]
for i in diff.itertuples():
    print("="*25)
    print(i.question1)
    print(i.question2)
    print(f"Original:{i.orig}")
    print(f"Predicted:{i.pred}")

What are some differences between German and Austrian culture?
What are the cultural differences between Austria and Germany?
Original:1
Predicted:0
What's your favorite idea?
What are your favorite Google-X like ideas?
Original:0
Predicted:1
How does Balaji Vishwanathan manage to answer every question? How does he keep himself updated about every topic?
How does Balaji vishwanathan stay updated with current affairs in every topic?
Original:1
Predicted:0
How much coffee does a coffee shop sell per day?
How many cups of coffee does the average coffee shop sell per day in the US?
Original:0
Predicted:1
What is the best way to get experience in cyber security?
How can I get into Internet security?
Original:1
Predicted:0
How do you log in to Facebook if you forgot your password?
How can I open my Facebook account I forgot my password and Gmail?
Original:1
Predicted:0
What is the best way to obtain full custody of a child?
How do I amend child custody order?
Original:0
Predicted:1
How shoul

Should I ask her out?
When should I ask her out?
Original:0
Predicted:1
Who was Babar?
Do you know Babar?
Original:1
Predicted:0
How can I stop being so desperate to have a girlfriend?
How can I stop being so desperate to have a girlfriend in India?
Original:1
Predicted:0
How can I forward, by selecting multiple emails, messages from my gmail inbox to one mail ID?
How do I delete all the emails in my Gmail inbox by one action only?
Original:0
Predicted:1
What would a conventional war between the US and Russia look like?
Who will win if there is non nuclear war between Russia and America?
Original:1
Predicted:0
What is the difference between UK, Britain, and England?
Is England in Britain? What is the difference between England, Britain and the UK?
Original:0
Predicted:1
What is a good way to say 寒冷的西伯利亚 in English?
How do you say ‘prodotto notevole’ in English?
Original:0
Predicted:1
What do you do if you can't remember your email or password to you snapchat account?
What should I do i

Is there a Japanese equivalent to Facebook?
Original:0
Predicted:1
Who are some of the best people to follow on Quora?
Who should I follow on Quora? Why?
Original:0
Predicted:1
How do I see people I unfollow on Instagram?
How do I unfollow a lot of people on Instagram, fast?
Original:0
Predicted:1
How do I download full versions of Korean dramas with English subtitles for free?
Where do I get to download full korean dramas with English subtitles?
Original:0
Predicted:1
Why is religion bad?
Is religion bad for you?
Original:1
Predicted:0
Would Infinite temperature have infinite heat (energy)?
Why do we say that negative temperature is hotter than infinite temperature? Wouldn't that mean it has infinite heat (and energy)?
Original:0
Predicted:1
Is at least the potential energy of vacuum energy and dark energy infinite?
Is vacuum energy the same as dark energy? is it infinite? if it is, how and why?
Original:1
Predicted:0
How do I sell an app in Google Play?
What are good ways to promote 

Predicted:1
How do I control the speed of a DC induction motor?
How control speed of induction motor?
Original:0
Predicted:1
What is wrong with our society today?
What's wrong with todays era?
Original:0
Predicted:1
What are the best ayurvedic hospitals in Kerala for Endometritis?
What are the best ayurvedic hospitals at Kerala for cervical spondilytis?
Original:0
Predicted:1
What should be an ideal learning experience/education system for a child?
What is the ideal education system like for the post-industrial era?
Original:1
Predicted:0
Why am I angry with everyone?
Why am I angry with myself?
Original:0
Predicted:1
Do this person feel­ same attractions tow­ards me 17/11/1993­ okara Pakistan, he 2­3/2/1997 rawalpindi P­akistan, mine time of birth is 4pm his 7am?
Do this person feel same attractions towards me me 17/11/1993 okara Pakistan, he 23/2/1997 rawalpindi Pakistan?
Original:1
Predicted:0
Can urinary incontinence be serious?
Is urinary incontinence serious?
Original:1
Predicted

What are the advantages of GST for the Indian economy?
Original:1
Predicted:0
Are you happy with the people around you?
Why will people be around you only when you are happy?
Original:0
Predicted:1
What happens once Ordinance is replaced by a bill? What does this mean for NEET 2016?
Has MH CET been replaced by NEET for 2016?
Original:0
Predicted:1
Do new 2000 INR really have a NGC (Nano GPS Chip), or is it just a rumour?
Are the notes of Rs. 2000 really embedded with a GPS chip?
Original:1
Predicted:0
What is the salary of iit professors?
How much salary do IIT professors get?
Original:1
Predicted:0
Does anyone regret becoming a doctor?
Do some doctors regret becoming doctors? Why? How common is this?
Original:1
Predicted:0
How do I get a puppy?
How can you get a puppy for free?
Original:0
Predicted:1
Bestiality on farms in Britain is not considered controversial. Is this true?
Bestiality in Britain is not considered controversial. Is this true?
Original:1
Predicted:0
What is the best 

...

Original:0
Predicted:1
Why do cats get scared when you place a cucumber in front of it?
Why cats scared by cucumbers?
Original:1
Predicted:0
How can I get a neighbor's WiFi password?
How can I get a WiFi password?
Original:0
Predicted:1
Why did Lord Rama break the bow of Lord Shiva?
Why  did Lord Rama break the bow of Siva?
Original:1
Predicted:0
Is Taylor Swift a bad example for teenage girls?
In what ways is Taylor Swift a good / bad role model for young women?
Original:1
Predicted:0
What is the most rational evidence, if there is any, of the existence of God?
Is there any proof which can be given for the existence of the GOD? If yes, what are those?
Original:1
Predicted:0
How do I write effective sales pitching emails?
How can I write an effective sales pitch?
Original:0
Predicted:1
What business can I start with INR 50000 rs?
What is the best idea to start a business with capital of 50000?
Original:1
Predicted:0
How can you improve the fine motor skills in preschoolers?
What are so

Original:0
Predicted:1
What is the slope when deflection is maximum in beam ?
What is slope and deflection in beams?
Original:0
Predicted:1
What are good substitutes for vegetable oil?
What is the best substitute for vegetable oil? Why is it considered to be the best?
Original:1
Predicted:0
Which country invented the sandwich?
Which country invented the pancake?
Original:0
Predicted:1
What are the best Web design courses?
What are the best courses for Web designing?
Original:1
Predicted:0
What is the best way to improve on English spellings?
How can we improve our English and avoid spelling mistakes?
Original:1
Predicted:0
How do I connect my PC's internet to my Windows Phone via USB or via Bluetooth?
How do I connect my mobile phone calls to the PC via Bluetooth?
Original:0
Predicted:1
How do get new snapchat filters?
How do I create a Snapchat filter?
Original:0
Predicted:1
Should people be allowed to kill themselves?
Why doesn't society allow depressed people to kill themselves?
Ori

Should people use Twitter less or more often?
Why do people use Facebook more than Twitter?
Original:0
Predicted:1
How do I prepare for the IELTS?
What is the best way to prepare for IELTS?
Original:0
Predicted:1
How can one invest ₹10,000, and in what way?
How do I invest ₹10,000?
Original:1
Predicted:0
How were the Pyramids of Giza built?
How were the pyramids in ancient Egypt built?
Original:1
Predicted:0
Which is better to treat pain, Advil or Aleve or Tylenal?
Which is better to treat pain, Advil or Aleve?
Original:0
Predicted:1
What are the reactions when a girl gets pregnant?
When does a girl gets pregnant?
Original:0
Predicted:1
Can we use solar panels without battery?
Can our solar panels be used with other stars?
Original:0
Predicted:1
What is the best question you have asked on Quora?
What is the best question that I can ask on Quora?
Original:0
Predicted:1
Which penny stocks are worth investing in India?
Are penny stocks good to invest in?
Original:1
Predicted:0
How do emot

What could be the best possible diet plan for gaining healthy weight?
What daily diet should I follow to gain weight?
Original:1
Predicted:0
House of Cards Season 2: Why was Frank so interested in the Civil War?
House of Cards Season 2: Why is Raymond Tusk interested in birds?
Original:0
Predicted:1
What is the cheapest way to travel from India to Europe?
What is the cheapest way to get product from india?
Original:0
Predicted:1
Which countries have free higher education?
Which countries offer free university education for international students?
Original:1
Predicted:0
How should I look confident?
How can I be and look confident?
Original:0
Predicted:1
Which Big Bang Theory character do you pity the most?
Which character on the Big Bang Theory is the most loved?
Original:0
Predicted:1
How can I delete photos from my Gmail account?
How do I erase a Gmail account from another phoned?
Original:0
Predicted:1
What was Marc Srour like as a teenager?
What is it like to be Marc Srour?
Original

What is the hyperechoic area? How is it determined?
How do hypoechoic and hyperechoic differ?
Original:0
Predicted:1
Is realvision worth the cost?
Is Nutanix worth the cost?
Original:0
Predicted:1
Why are some people just so evil?
Why are some people evil? Are they born that way or does life make them evil?
Original:0
Predicted:1
Do sociopaths commit suicide?
Is it true that sociopaths don't commit suicide?
Original:0
Predicted:1
Which app is best for free online dating?
What is best free dating app?
Original:1
Predicted:0
How do I study Tao Te Ching?
Why do you like Tao Te Ching?
Original:0
Predicted:1
What was the best day of your life? (Excluding family things like births)
Can you describe the best moment or the best day in your life?
Original:1
Predicted:0
Will India ever get free healthcare?
Can India ever have free healthcare system like Australia, UK, Netherlands, New Zealand, Ireland etc. have?
Original:1
Predicted:0
Why does hot water appear white-ish in colour?
Why does hot w